# Polaron calculations using EPWpy

<table>
<tr>
<td width="50%">

Author: **Jon Lafuente-Bartolome**


In this notebook, we perform calculations of polarons. The theory and computational method are described in [Phys. Rev. Lett. **122**, 246403 (2019)](https://doi.org/10.1103/PhysRevLett.122.246403) and [Phys. Rev. B **99**, 235139 (2019)](https://doi.org/10.1103/PhysRevB.99.235139).

Electrons and phonons are computed with Quantum ESPRESSO (QE), maximally-localized Wannier functions are computed with Wannier90, and electron-phonon matrix elements and polarons are computed with EPW.     
    
</td>
<td width="50%">

**MATCSSI**

<img src="https://matcssi.tacc.utexas.edu/media/filer_public_thumbnails/filer_public/9f/1e/9f1ebcd2-8f80-4142-bcdf-b9c262c6b62d/matccsi-home-banner.jpg__1400x1400_q85_subsampling-2.jpg" width="1000">

For running production calculations
please visit [MATCSSI](https://matcssi.tacc.utexas.edu/)


</td>
</tr>
</table>

## **NOTE:**
The calculations in this notebook are for demonstration purposes only and are not converged.
For any production-quality results, be sure to perform full convergence tests with respect to all relevant parameters.

## **Step 1: Get linux packages to build QE**
Skip this step if you already have all these libraries installed.

Note: In a single session you need this once!

In [ ]:
!apt-get -y update
!apt-get -y install m4 make wget curl git gfortran gcc libopenblas-dev libfftw3-dev libopenmpi-dev tar libxrender1

## Get EPWpy
We clone it from GitLab and then install QE+EPW inside EPWpy



In [ ]:
%cd /content
#!pip uninstall EPWpy-basic # Use this if you have multiple EPWpy versions installed
!git clone https://gitlab.com/epwpy/epwpy.git


## Checkout to current branch and install QE

In [ ]:
%cd /content/epwpy
!git checkout sabyadk/EPWpy_v1.1_n
!python setup.py install --withQE True --configs 'with-scalapack=no DFLAGS="-D__FFTW3 -D__MPI" FFT_LIBS="-lfftw3"' --cores 1


## Check if we have all the executables for QE+EPW installed by EPWpy
We also check the version of EPWpy which should be 1.1


In [ ]:
!ls /content/epwpy/build/q-e-EPW-5.9s/bin/
!pip show EPWpy-basic


## Calculations of self-trapped polarons

In this notebook we calculate the formation energy, wave function, and atomic displacements of self-trapped polarons in LiF using the [*ab initio* polaron equations](https://doi.org/10.1103/PhysRevB.99.235139).

Install some extra packages:

In [ ]:
!pip install mp-api

### **Restart** kernel before starting calculations so that the installations take effect

Load required modules:

In [ ]:
from EPWpy import EPWpy as EP
from EPWpy.utilities import EPW_util
from EPWpy.plotting import plot_polaron
import numpy as np

### Define EPWpy object

Define general calculation parameters to be used throughout the workflow:

In [ ]:
# Set prefix
prefix='lif'

# Maximum number of cores to be used
cores = 1
print('Maximum number of cores to be used:', cores)

# Define EPWpy object
lif=EP.EPWpy({'prefix':'\''+prefix+'\'',
           'calculation':'\'scf\'',
           'ibrav':2,
           'nat':2,
           'ntyp':2,
           'atomic_species':['Li', 'F'],
           'atomic_pos':np.array([[0.0, 0.0, 0.0],
                                  [-0.5, 0.5, 0.5]]), # in alat
           'mass':[6.941, 18.9984],
           'atoms':['Li', 'F'],
           'ecutwfc':'80',
           'celldm(1)':'7.67034',
           'pseudo_auto':True},
           system='lif')

# Set running parameters
lif.run_serial = True

Visualize crystal structure:

In [ ]:
print(lif.structure_params_summary)

In [ ]:
app = lif.display_lattice(supercell=[3,3,3],view={'wrap':False,
                                                  'show_bond_length':False,
                                                  'bond_length':2.5,
                                                  'bond_color':'g',
                                                  'atom_size_factor':100})

### Run scf, ph, and nscf calculations

Here we perform the self-consistent field calculation to obtain the electron charge density of LiF in the ground state.
The calculation consists of three separate steps:
1. Apply the method `scf` to the object `lif`. This step specifies runtime parameters for the scf calculation.
2. Based on the properties defined at step 1 as well as other properties that are set by default within EPWpy, the method `prepare` creates the input file needed by QE.
3. The method `run` applied to the object `lif` instructs QE to perform the SCF calculation.

In [ ]:
# scf calculation
lif.env = ''  # We don't have mpi in google colab
lif.scf(electrons={'conv_thr':'1.0d-12'}, kpoints={'kpoints':[[4, 4, 4]]}, name='scf')
lif.prepare(type_run='scf')
lif.run(cores, type_run='scf', parallelization='-nk 1')

Now we repeat a similar procedure for the phonon (`ph`) calculations on a coarse grid:

In [ ]:
# ph calculation
lif.ph(phonons={'nq1':3,
                'nq2':3,
                'nq3':3})
lif.prepare(type_run='ph')
lif.run(cores, type_run='ph', parallelization='-nk 1')

And proceed similarly for the `nscf` calculation:

In [ ]:
# nscf calculation
lif.nscf(system={'nbnd':15},
         kpoints={'grid':[6, 6, 6],
                  'kpoints_type': 'crystal'})
lif.prepare(type_run='nscf')
lif.run(cores, type_run='nscf', parallelization=' -nk 1')

### EPW calculations on the coarse mesh

Now we calculate the electron-phonon matrix elements in the coarse mesh, and transform them to the Wannier representation.

We then proceed as in the other calculations.
First, we apply the method `epw` to the object `lif`. This step specifies runtime parameters for the EPW calculation.
Then, we apply the method `prepare` to generate the input file, and `run` to perform the calculation.

In [ ]:
# epw coarse-mesh calculation
#
# set epw input variables
lif.epw(epwin={'wannierize':'.true.',
               'nbndsub':'3',
               'bands_skipped':'\'exclude_bands = 1:2, 6:15\'',
               'proj':['\'F : p\''],
               'wannier_plot':'.true.',
               'band_plot':'.true.',
               'lpolar':'.true.',
               'filkf':'\'./path.kpt\'',
               'filqf':'\'./path.kpt\'',
                },
        name='epw1')
#
# Generate filkf if needed
W=[0.5,0.75,0.25]
L=[0.0,0.5,0.0]
G=[0.0,0.0,0.0]
X=[0.5,0.5,0.0]
K=[0.375,0.75,0.375]
sympoints=[W,L,G,X,W,K]
lif.filkf(path=sympoints, length=[41, 41, 41, 41, 41], name='path.kpt')
#
# prepare and run
lif.prepare(type_run='epw1')
lif.run(cores, type_run='epw1')

### Interpolation to fine mesh and solution of polaron equations

We now proceed with the interpolation onto a fine reciprocal-space grid, and the self-consistent solution of the polaron equations.
We prepare a `epw2` file to separate from the coarse-mesh calculation.

In [ ]:
lif.epw(epwin={'bands_skipped':'\'exclude_bands = 1:2, 6:15\'',
               'nbndsub':3,
               'lpolar':'.true.',
               'plrn':'.true.',
               'restart_plrn':'.false.',
               'type_plrn':1,
               'init_plrn':1,
               'init_sigma_plrn':1.0,
               'niter_plrn':500,
               'conv_thr_plrn':1.0E-4,
               'ethrdg_plrn':1.0E-6,
               'adapt_ethrdg_plrn':'.true.',
               'init_ethrdg_plrn':1.0E-4,
               'nethrdg_plrn':20,
#               'io_lvl_plrn':0,
               'nkf1':6, 'nkf2':6, 'nkf3':6,
               'nqf1':6, 'nqf2':6, 'nqf3':6},
            name='epw2')
lif.prepare(1, type_run='epw2')
lif.run(cores, type_run='epw2')

### Visualization and post-processing

Once the polaron solution has been found, we can visualize its wave function and associated lattice displacements in real space, as well as their corresponding expansion coefficients in reciprocal space.

In [ ]:
# epw post-processing
lif.epw(epwin={'bands_skipped':'\'exclude_bands = 1:2, 6:15\'',
               'nbndsub':3,
               'lpolar':'.true.',
               'plrn':'.true.',
               'restart_plrn':'.true.',
               'type_plrn':1,
               'cal_psir_plrn':'.true.',
               'step_wf_grid_plrn':4,
               'interp_Ank_plrn':'.true.',
               'interp_Bqu_plrn':'.true.',
               'filkf':'\'./path.kpt\'',
               'filqf':'\'./path.kpt\'',
               'nkf1':6, 'nkf2':6, 'nkf3':6,
               'nqf1':6, 'nqf2':6, 'nqf3':6},
            name='epw3')
lif.prepare(1,type_run='epw3')

In [ ]:
# Run post-processing
lif.run(cores, type_run='epw3')

### Plot polaron wave function

We can visualize the polaron in real space, where arrows show the atomic displacements and the isosurface shows the polaron wave function.

In [ ]:
lif_util = lif.EPW_utilities() # Get the EPW utility first
lif_util.plot_polaron(view={'quiver_length':10,
                            'depthshape':False,
                            'pos_alpha':1,
                            'atom_size_factor':30})

### Plot expansion coefficients

We can plot the interpolated expansion coefficients along a path in reciprocal space. We will use the same `path.kpt` file generated before:

In [ ]:
# Plot Ank coefficients
plot_polaron.plot_Ank_Bqv('Ank', prefix+'/epw/path.kpt', sympoints, prefix+'/epw/Ank.band.plrn')

In [ ]:
# Plot Bqv coefficients
plot_polaron.plot_Ank_Bqv('Bqv', prefix+'/path.kpt', sympoints, prefix+'/epw/Bmat.band.plrn')

## Extrapolation to the isolated polaron limit ($N_p\rightarrow\infty$)

The previous solution was obtained for a given reciprocal-space grid / real-space supercell.
To account for the spurious interactions between periodic images of polarons, we need to perform calculations on increasingly dense meshes and extrapolate to the dilute polaron limit.

We first define the grids we want to consider in which the corresponding formation energies will be computed, and prepare the input files:

In [ ]:
# List of k-point meshes to consider
klist = [6, 8, 10]

for k in klist:
    lif.epw(epwin={'bands_skipped':'\'exclude_bands = 1:2, 6:15\'',
                   'nbndsub':3,
                   'lpolar':'.true.',
                   'plrn':'.true.',
                   'restart_plrn':'.false.',
                   'type_plrn':1,
                   'init_plrn':1,
                   'init_sigma_plrn':1.0,
                   'niter_plrn':500,
                   'conv_thr_plrn':1.0E-4,
                   'ethrdg_plrn':1.0E-6,
                   'adapt_ethrdg_plrn':'.true.',
                   'init_ethrdg_plrn':1.0E-4,
                   'nethrdg_plrn':20,
                   'nkf1':str(k), 'nkf2':str(k), 'nkf3':str(k),
                   'nqf1':str(k), 'nqf2':str(k), 'nqf3':str(k)},
            name='epw4.'+str(k))

    #
    lif.prepare(type_run='epw3', name = 'epw', infile='epw4.'+str(k)+'.in')

We now run the calculations for each grid:

In [ ]:
# Run calculations
lif.run_serial=True
for k in klist:
    lif.run(cores, type_run='epw3', infile='epw4.'+str(k))

Now we perform a linear extrapolation to the infinite supercell limit from the computed data points:

In [ ]:
# Set unit cell volume in Bohr^3 (to convert Nk to inverse supercell size)
ucell_volume = 112.8044

# Read formation energies from output files
Eform = []
for k in klist:
    lif.epw_file = 'epw4.'+str(k)
    Eform.append(lif.Eform)

Nk = np.array(klist)
Eform = np.array(Eform)

# Plot
plot_polaron.plot_EvsNk(ucell_volume, Nk, Eform)

## Polaron hopping barrier calculation

### Relatively dense grid calculation

In [ ]:
# Prepare epw input for fine mesh interpolation and polaron calculation
lif.epw(epwin={'bands_skipped':'\'exclude_bands = 1:2, 6:15\'',
               'nbndsub':3,
               'etf_mem':0,
               'lpolar':'.true.',
               'plrn':'.true.',
               'restart_plrn':'.false.',
               'type_plrn':1,
               'init_plrn':1,
               'init_sigma_plrn':1.0,
               'niter_plrn':500,
               'conv_thr_plrn':1.0E-4,
               'ethrdg_plrn':1.0E-6,
               'adapt_ethrdg_plrn':'.true.',
               'init_ethrdg_plrn':1.0E-4,
               'nethrdg_plrn':20,
               'nkf1':6, 'nkf2':6, 'nkf3':6,
               'nqf1':6, 'nqf2':6, 'nqf3':6},
            name='epw2')
#
lif.prepare(type_run='epw2')
lif.run(cores, type_run='epw2')

### Shift the polaron displacement pattern by one unit cell

In [ ]:
import os
print(os.getcwd())
prefix=lif.prefix
print(prefix+'/epw/dtau.plrn')

# Read the dtau.plrn
dtau = EPW_util.read_dtau_plrn(prefix+'/epw/dtau.plrn')
# Shift it along x by one unit cell
shift_x = EPW_util.generate_dtau_disp(dtau, direction='x')
# Generate and all the intermediate structures
ntau = 21
EPW_util.write_dtau_disp(dtau, shift_x, ntau, fileout=prefix + '/epw/dtau_disp.plrn_')

#### Perform polaron calculations and save the total energy for all intermediate atomic displacement configurations

In [ ]:
# Prepare epw input for energy landscape calculation
lif.epw(epwin={'etf_mem':0,
               'bands_skipped':'\'exclude_bands = 1:2, 6:15\'',
               'nbndsub':3,
               'plrn':'.true.',
               'restart_plrn':'.false.',
               'type_plrn':1,
               'init_plrn':6,
               'init_ntau_plrn':str(ntau),
               'init_sigma_plrn':1.0,
               'niter_plrn':1,
               'conv_thr_plrn':1.0E-4,
               'ethrdg_plrn':1.0E-6,
               'adapt_ethrdg_plrn':'.true.',
               'init_ethrdg_plrn':1.0E-4,
               'nethrdg_plrn':20,
               'io_lvl_plrn':0,
               'nkf1':6,
               'nkf2':6,
               'nkf3':6,
               'nqf1':6,
               'nqf2':6,
               'nqf3':6,
               'lpolar':'.true.',
               'eig_read':'.false.'},
            name='epw2.dtau')

# Prepare input file
lif.prepare(1, type_run='epw2', name='epw', infile='epw2.dtau.in')

# Run epw calculation
lif.run(cores, type_run='epw2', infile='epw2.dtau')

#### Plot the potential surface and extract the hopping barrier

In [ ]:
import matplotlib.pyplot as plt
prefix=lif.prefix
E_pot_surf = []
file = open(prefix + '/epw/epw2.dtau.out', 'r')
for line in file:
    if "Formation Energy at this " in line:
        E_pot_surf.append( float(line.split()[-1]) )
file.close()

font = {'family' : 'DejaVu Sans',
    'size'   : 36}
plt.rc('font', **font)

fig, ax = plt.subplots(1, figsize=(12,8))
scaling = np.linspace(0,1,ntau)
ax.plot(scaling, E_pot_surf, marker='o', markersize=10, linewidth=5, color='black')
ax.set_xlabel('Reaction coordinate')
ax.set_ylabel('Formation energy (eV)')

plt.show()


E_barrier = max(E_pot_surf) - min(E_pot_surf)

print('Hopping barrier (eV): ', E_barrier)